In [ ]:
# use the latest version of folium
#!pip install -U folium
!pip install git+https://github.com/python-visualization/folium.git
!pip install geopandas
!pip install geojson

  Cloning https://github.com/python-visualization/folium.git to /tmp/pip-req-build-r7cm4o7i
  Running command git clone -q https://github.com/python-visualization/folium.git /tmp/pip-req-build-r7cm4o7i
  Created wheel for folium: filename=folium-0.11.0+19.g46f820e-py2.py3-none-any.whl size=97533 sha256=d504a980c4bdc652f88203ebf710d0a9e53434bd788de70aba42dc1ba2bdaa7b
  Stored in directory: /tmp/pip-ephem-wheel-cache-jm0bt_kf/wheels/e7/9d/fb/0526aecb47b5ed7e199de000ffa4ba9af6b30ad365c4802813
Successfully built folium
ERROR: datascience 0.10.6 has requirement folium==0.2.1, but you'll have folium 0.11.0+19.g46f820e which is incompatible.
  Found existing installation: folium 0.11.0
    Uninstalling folium-0.11.0:
      Successfully uninstalled folium-0.11.0


In [ ]:
import os
import folium
import branca
import requests
import json
import geopandas as gpd
import pandas as pd
import folium.plugins as plugins
from folium.features import GeoJson, GeoJsonTooltip, GeoJsonPopup
import numpy as np
import geojson
import gzip

In [ ]:
#! git clone https://gitlab.com/steven.horn/covid-prevalence.git --depth 1 --branch latest --single-branch /content/covid-prevalence-latest
! git clone https://gitlab.com/steven.horn/covid-prevalence.git --depth 1 --branch master --single-branch /content/covid-prevalence
! git clone https://github.com/ishaberry/Covid19Canada.git --depth 1 --branch master --single-branch /content/Covid19Canada
! git clone https://github.com/CSSEGISandData/COVID-19.git --depth 1 --branch master --single-branch /content/COVID-19

fatal: destination path '/content/covid-prevalence' already exists and is not an empty directory.


In [ ]:
mapfile = '/content/covid-prevalence/data/Health_Regional_Archive__Public_View_.geojson.gz'

with gzip.open(mapfile, mode='rb') as f:
  map_data = f.read()

data = json.loads(map_data)


In [ ]:

#url = r'https://opendata.arcgis.com/datasets/3aa9f7b1428642998fa399c57dad8045_0.geojson'
#json_data = requests.get(url).text
#geo_json_data = json.loads(requests.get(url).text)
#map = geojson.loads(json_data)

#response = requests.get(url)
#data = response.json()

filepath='/content/covid-prevalence/results/latest_results.csv'
df = pd.read_csv(filepath)
regions = gpd.GeoDataFrame.from_features(data, crs='EPSG:4326')

df['HR_UID']=df['HR_UID'].astype(int)
regions['HR_UID']=regions['HR_UID'].astype(int)

regions = pd.merge(regions,df, on="HR_UID")

regions['LogCurrentCaseCount'] = np.log(regions['CurrentCaseCount'])
regions['LogCurrentCaseCount'] = regions.apply(lambda x: x['LogCurrentCaseCount'] if x['CurrentCaseCount'] > 0 else 0, axis=1)

regions['LogPrevalence'] = np.log(regions['pointprevalence_50'])
regions['LogPrevalence'] = regions.apply(lambda x: x['pointprevalence_50'] if x['pointprevalence_50'] > 0 else 0, axis=1)

# need to do this to reduce file size
regions['geometry'] = regions['geometry'].simplify(0.005)
#regions['centroid'] = regions['geometry'].centroid
regions['centroidx'] = regions.apply(lambda x: x['geometry'].centroid.coords[0][0], axis=1)
regions['centroidy'] = regions.apply(lambda x: x['geometry'].centroid.coords[0][1], axis=1)

regions.head()

geometry  ...  centroidy
0  POLYGON ((-79.79317 43.30113, -79.77674 43.275...  ...  43.253385
1  MULTIPOLYGON (((-77.50018 43.91084, -77.51734 ...  ...  44.625050
2  POLYGON ((-81.51330 43.95285, -81.50723 43.957...  ...  43.599095
3  MULTIPOLYGON (((-81.87724 42.25009, -81.89665 ...  ...  42.417628
4  MULTIPOLYGON (((-77.07579 44.05670, -77.02191 ...  ...  44.658480

[5 rows x 61 columns]

In [20]:
colormap = branca.colormap.LinearColormap(
    vmin=0,#regions['LogPrevalence'].quantile(0.0), 
    vmax=0.1,#regions['LogPrevalence'].quantile(1), 
    #colors=['darkgreen','green','orange', 'red'],
    colors=['white','orange', 'red'],
    caption="Point prevalence",
)

In [11]:
#m = folium.Map(location=[35.3, -97.6], zoom_start=4)

#for index, row in regions.iterrows():
#  folium.Marker([row['centroidy'], row['centroidx']], popup=popup).add_to(m)
"%.2f" % (1.12345)
#m

'1.12'

In [21]:
m = folium.Map(location=[48.3, -95.6], 
               tiles='Stamen Toner', 
               zoom_start=4)

tooltip = GeoJsonTooltip(
    fields=["ENGNAME", "HR_UID", "CurrentCaseCount", "pointprevalence_50", "pointprevalence_50"],
    aliases=["Region:", "HR_UID", "Current Case Count :", "Prevalence:", "Infectious Prevalence:"],
    localize=True,
    sticky=False,
    labels=True,
    style="""
        background-color: #F0EFEF;
        border: 2px solid black;
        border-radius: 3px;
        box-shadow: 3px;
    """,
    max_width=800,
)

popup = GeoJsonPopup(
    fields=['ENGNAME','CurrentTests'],
    aliases=['Region',"Current Tests"],
    localize=True,
    labels=True,
    style="background-color: yellow;",
)

g = folium.GeoJson(
    regions,
    style_function=lambda x: {
        "fillColor": colormap(x["properties"]["pointprevalence_50"])
        if x["properties"]["pointprevalence_50"] is not None
        else "transparent",
        "color": "black",
        "fillOpacity": 0.4,
    },
    tooltip=tooltip,
    zoom_on_click=False
    #popup=popup
)#.add_to(m)

colormap.add_to(m)

#      <a class="btn btn-primary" href="">Open Group Risk Tool</a>

for index, row in regions.iterrows():
  html = """<h1>%s: %s</h1>
     <img src='https://stevenhorn.gitlab.io/covid-prevalence/results/latest/%s/%s_prev.png'><br/>
     <img src='https://stevenhorn.gitlab.io/covid-prevalence/results/latest/%s/%s_fit.png'><br/>
     <img src='https://stevenhorn.gitlab.io/covid-prevalence/results/latest/%s/%s_lambda.png'>
  """ % (row['Province'],row['ENGNAME'], row['nameid'],row['nameid'],row['nameid'],row['nameid'],row['nameid'],row['nameid'])
  iframe = branca.element.IFrame(html=html, width=500, height=400)
  ppopup = folium.Popup(iframe, max_width=500)
  folium.Marker([row['centroidy'], row['centroidx']], 
                popup=ppopup, 
                icon=folium.Icon(color='lightgray', icon='info-circle', prefix='fa'))#.add_to(m)

  tooltiphtml = """
    %s<br/>Point-prevalence: %.2f (%.2f - %.2f)<br/><img width='300px' height='200px' src='https://stevenhorn.gitlab.io/covid-prevalence/results/latest/%s/%s_prev.png'>
    """ % ( row['ENGNAME'], row['pointprevalence_50'], row['pointprevalence_05'],row['pointprevalence_95'], row['nameid'], row['nameid'])
  
  zone = folium.GeoJson(
    regions.loc[lambda df: df['nameid'] == row['nameid']],
    style_function=lambda x: {
        "fillColor": colormap(x["properties"]["pointprevalence_50"])
        if x["properties"]["pointprevalence_50"] is not None
        else "transparent",
        "color": "black",
        "fillOpacity": 0.4,
    },
    tooltip=tooltiphtml,
    zoom_on_click=False
  )
  ppopup.add_to(zone)
  #zone.zoom_on_click=False
  zone.add_to(m)

  #folium.Circle(
  #    location=[row['centroidy'], row['centroidx']],
  #    popup=ppopup,
  #    radius=5,#row['CurrentCaseCount']*3000,
  #    color='crimson',
  #    fill=True,
  #    fill_color='crimson'
  # ).add_to(m)
  
plugins.Fullscreen(
    position='topright',
    title='Expand me',
    title_cancel='Exit me',
    force_separate_button=True
).add_to(m)

m.save(os.path.join('/content/drive/My Drive', 'map.html'))



In [22]:
m

In [ ]:
m = folium.Map([43, -100], zoom_start=4)
html = """
     <img src='https://stevenhorn.gitlab.io/covid-prevalence/results/latest/CanadaOntarioOttawa/CanadaOntarioOttawa_prev.png'>
    """

iframe = branca.element.IFrame(html=html, width=500, height=300)
popup = folium.Popup(iframe, max_width=500)

folium.Marker([45.4215, -75.6972], popup=popup).add_to(m)

plugins.Fullscreen(
    position='topright',
    title='Expand me',
    title_cancel='Exit me',
    force_separate_button=True
).add_to(m)

#folium.GeoJson(url).add_to(m)
m.save(os.path.join('/content', 'demo.html'))

m

In [ ]:
import geopandas as gpd

assert 'naturalearth_lowres' in gpd.datasets.available
datapath = gpd.datasets.get_path('naturalearth_lowres')
gdf = gpd.read_file(datapath)

In [ ]:



n_periods, n_sample = 48, 40

assert n_sample < n_periods

datetime_index = pd.date_range('2016-1-1', periods=n_periods, freq='M')
dt_index_epochs = datetime_index.astype(int) // 10**9
dt_index = dt_index_epochs.astype('U10')

dt_index

import numpy as np

styledata = {}

for country in gdf.index:
    df = pd.DataFrame(
        {'color': np.random.normal(size=n_periods),
         'opacity': np.random.normal(size=n_periods)},
        index=dt_index
    )
    df = df.cumsum()
    df.sample(n_sample, replace=False).sort_index()
    styledata[country] = df

max_color, min_color, max_opacity, min_opacity = 0, 0, 0, 0

for country, data in styledata.items():
    max_color = max(max_color, data['color'].max())
    min_color = min(max_color, data['color'].min())
    max_opacity = max(max_color, data['opacity'].max())
    max_opacity = min(max_color, data['opacity'].max())

from branca.colormap import linear
cmap = linear.PuRd_09.scale(min_color, max_color)

def norm(x):
    return (x - x.min()) / (x.max() - x.min())

for country, data in styledata.items():
    data['color'] = data['color'].apply(cmap)
    data['opacity'] = norm(data['opacity'])

styledata.get(0).head()
styledict = {
    str(country): data.to_dict(orient='index') for
    country, data in styledata.items()
}

In [ ]:
from folium.plugins import TimeSliderChoropleth
f = folium.Figure()#width=1000, height=600)
m = folium.Map(location= [0, 0], tiles="stamentoner",
zoom_start=2, min_zoom = 2).add_to(f)

#m = folium.Map([0, 0], tiles='Stamen Toner', zoom_start=2)

g = TimeSliderChoropleth(
    gdf.to_json(),
    styledict=styledict,
    overlay=True,
).add_to(m)

html = """
     <img src='/results/latest/CanadaOntarioOttawa/CanadaOntarioOttawa_prev.png'>
    """

iframe = branca.element.IFrame(html=html, width=500, height=300)
popup = folium.Popup(iframe, max_width=500)

folium.Marker([45.4215, -75.6972], popup=popup).add_to(m)
#folium.LayerControl(collapsed=False).add_to(m)

m.save(os.path.join('/content', 'TimeSliderChoropleth.html'))

m

In [ ]:



np.random.seed(3141592)

initial_data = (
    np.random.normal(size=(100, 2)) * np.array([[0.4, 0.4]]) +
    np.array([[45.4215, -75.6972]])
)

move_data = np.random.normal(size=(100, 2)) * 0.01

data = [(initial_data + move_data * i).tolist() for i in range(100)]

weight = 5  # default value
for time_entry in data:
    for row in time_entry:
        row.append(weight)


from datetime import datetime, timedelta

time_index = [
    (datetime.now() + k * timedelta(1)).strftime('%Y-%m-%d') for
    k in range(len(data))
]

m = folium.Map([45.4215, -75.6972], tiles='stamentoner', zoom_start=4)

hm = plugins.HeatMapWithTime(
    data,
    min_speed=5,
    max_speed=30,
    speed_step=1,
    radius=30,
    index=time_index,
    auto_play=True,
    max_opacity=0.3
)

hm.add_to(m)

m.save(os.path.join('/content', 'hm.html'))

m